In [1]:
import os
import json

import numpy as np
import pandas as pd

In [3]:
DUMP_DIR = "../../dumps/expC_dist_learner_for_adv_ex/rdm_concspheres_test/attack_perfs_on_runs/all_attack_perfs_fixed_07022022//"

In [4]:
th_analyze = np.arange(1e-2, 1.6e-1, 1e-2) # if model is distance learner, then thresholds to analyse performance
# th_analyze = np.array([1e-2])
th_analyze = np.append(th_analyze, np.inf)

In [5]:
print(th_analyze)

[0.01 0.02 0.03 0.04 0.05 0.06 0.07 0.08 0.09 0.1  0.11 0.12 0.13 0.14
 0.15  inf]


In [6]:
os.listdir(DUMP_DIR)


['rdm_concspheres_k2n500_noninfdist_moreoffmfldv2-regression.json',
 'rdm_concspheres_k2n500_noninfdist_moreoffmfld-regression.json',
 'rdm_concspheres_k2n500_noninfdist_upmn-regression.json',
 'rdm_concspheres_k2n500_noninfdist_upmn-clf.json',
 'rdm_concspheres_k50n500_noninfdist-clf.json',
 'rdm_concspheres_k50n500_noninfdist_moreoffmfld-regression.json',
 'rdm_concspheres_k2n500_noninfdist-regression.json',
 'rdm_concspheres_k3n500_noninfdist_moreoffmfld-regression.json',
 'rdm_concspheres_k50n500_noninfdist-regression.json',
 'rdm_concspheres_k2n500_noninfdist-clf.json',
 'rdm_concspheres_k500n500_noninfdist_moreoffmfld-regression.json',
 'rdm_concspheres_k500n500_noninfdist-regression.json',
 'rdm_concspheres_k3n500_noninfdist_moreoffmfld-clf.json',
 '.ipynb_checkpoints',
 'rdm_concspheres_k2n500_noninfdist_moreoffmfld-regression-Copy1.json',
 'rdm_concspheres_k500n500_noninfdist-clf.json']

In [7]:
master_df = None
file = os.listdir(DUMP_DIR)[-6]
master_df = pd.read_json(os.path.join(DUMP_DIR, file), orient="records")
master_json = None
with open(os.path.join(DUMP_DIR, file)) as f:
    master_json = json.load(f)

In [8]:
columns = master_df.columns
columns

Index(['atk_flavor', 'atk_routine', 'eps', 'eps_iter', 'nb_iter', 'norm',
       'restarts', 'verbose', 'k', 'n', 'max_norm', 'N', 'inp_dir', 'task',
       'ftname', 'tgtname', 'thresh', 'adv_clf_report', 'adv_abs_cm',
       'adv_pct_cm', 'clf_report', 'abs_cm', 'pct_cm', 'distance_sct_plt',
       'result_dir'],
      dtype='object')

In [9]:
unique_runs_to_check_for_thresh = master_df[master_df["task"] == "dist"]


In [10]:
master_df.shape, unique_runs_to_check_for_thresh.shape

((12800, 25), (12800, 25))

In [11]:
master_df["thresh"]

0         inf
1         inf
2         inf
3         inf
4         inf
         ... 
12795    0.11
12796    0.12
12797    0.13
12798    0.14
12799    0.15
Name: thresh, Length: 12800, dtype: float64

In [12]:
new_entries = list()
for idx, run in unique_runs_to_check_for_thresh.iterrows():
#     print(run)
    for th in th_analyze[:-1]:
        result_entry = {col: run[col] for col in columns}
        result_entry["thresh"] = th
        
        closest_extracted_th = None
        
        # distance_scatter_plots
        distance_scatter_plot_dir = os.path.join(run["result_dir"], "distance_scatter_plots_test")
        distance_scatter_plot_files = [i for i in os.listdir(distance_scatter_plot_dir) if "all" in i]
        all_extracted_th = list()
        for f in distance_scatter_plot_files:
            extracted_th = float(f.split("_")[-1].rstrip(".png").split("=")[1])
            all_extracted_th.append(extracted_th)
        
        diffs = [np.abs(i - th) for i in all_extracted_th]
        idx = np.argmin(diffs)
        
        closest_extracted_th = all_extracted_th[idx]
        print("thresh:", th, "closes_th:", closest_extracted_th)
        result_entry["thresh"] = closest_extracted_th
        
        result_entry["distance_sct_plt"] = os.path.join(distance_scatter_plot_dir, distance_scatter_plot_files[idx])
        assert(os.path.exists(os.path.join(distance_scatter_plot_dir, distance_scatter_plot_files[idx])))
        
        # adv_abs_cm
        abs_cm_dir = os.path.join(run["result_dir"], "abs_cm_plots_test")
        adv_abs_cm_file = os.path.join(abs_cm_dir, "adv_abs_cm_test_th={}.csv".format(closest_extracted_th))
        abs_cm_file = os.path.join(abs_cm_dir, "abs_cm_test_th={}.csv".format(closest_extracted_th))
        
        result_entry["abs_cm"] = abs_cm_file
        result_entry["adv_abs_cm"] = adv_abs_cm_file
        assert(os.path.exists(abs_cm_file))
        assert(os.path.exists(adv_abs_cm_file))
        
        # pct_abs_cm
        pct_cm_dir = os.path.join(run["result_dir"], "pct_cm_plots_test")
        adv_pct_cm_file = os.path.join(pct_cm_dir, "adv_pct_cm_test_th={}.csv".format(closest_extracted_th))
        pct_cm_file = os.path.join(pct_cm_dir, "pct_cm_test_th={}.csv".format(closest_extracted_th))
        assert(os.path.exists(pct_cm_file))
        assert(os.path.exists(adv_pct_cm_file))
        
        result_entry["pct_cm"] = pct_cm_file
        result_entry["adv_pct_cm"] = adv_pct_cm_file
        
        result_entry["adv_clf_report"] = None
        result_entry["clf_report"] = None
        new_entries.append(result_entry)

#     print(result_entry)
#     print(result_entry["thresh"])
#     print(result_entry["distance_sct_plt"])


thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thr

thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thr

thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thr

thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thr

thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thr

...

thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thr

thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thr

thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thr

thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
th

thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thresh: 0.08 closes_th: 0.08
thresh: 0.09 closes_th: 0.09
thresh: 0.09999999999999999 closes_th: 0.09999999999999999
thresh: 0.11 closes_th: 0.11
thresh: 0.12 closes_th: 0.12
thresh: 0.13 closes_th: 0.13
thresh: 0.14 closes_th: 0.14
thresh: 0.15000000000000002 closes_th: 0.15000000000000002
thresh: 0.01 closes_th: 0.01
thresh: 0.02 closes_th: 0.02
thresh: 0.03 closes_th: 0.03
thresh: 0.04 closes_th: 0.04
thresh: 0.05 closes_th: 0.05
thresh: 0.060000000000000005 closes_th: 0.060000000000000005
thresh: 0.06999999999999999 closes_th: 0.06999999999999999
thr

In [13]:
len(new_entries), th_analyze.shape

(192000, (16,))

In [15]:



FIXED_DF_DUMP = "../../dumps/expC_dist_learner_for_adv_ex/rdm_concspheres_test/attack_perfs_on_runs/all_attack_perfs/"
fixed_file = os.path.join(FIXED_DF_DUMP, file)
master_json.extend(new_entries)
print(fixed_file, len(master_json))
with open(fixed_file, "w") as f:
    json.dump(master_json, f)



../../dumps/expC_dist_learner_for_adv_ex/rdm_concspheres_test/attack_perfs_on_runs/all_attack_perfs_fixed_07022022/rdm_concspheres_k500n500_noninfdist_moreoffmfld-regression.json 12800


In [16]:
tmp = pd.DataFrame(new_entries)
tmp_list = tmp[tmp.thresh >= 0.15].abs_cm.tolist()

In [34]:
tmp_list[0] == tmp_list[15]

True

In [21]:
tmp_list

['/data/dumps/expC_dist_learner_for_adv_ex/rdm_concspheres_test/rdm_concspheres_k50n500_noninfdist/1/attack_perf/atk_flavor=std_pgd,atk_routine=my,eps=0.01,eps_iter=0.005,nb_iter=100,norm=2,restarts=1,verbose=False,task=dist/abs_cm_plots_test/abs_cm_test_th=0.15000000000000002.csv',
 '/data/dumps/expC_dist_learner_for_adv_ex/rdm_concspheres_test/rdm_concspheres_k50n500_noninfdist/1/attack_perf/atk_flavor=std_pgd,atk_routine=my,eps=0.01,eps_iter=0.005,nb_iter=100,norm=2,restarts=1,verbose=False,task=dist/abs_cm_plots_test/abs_cm_test_th=0.15000000000000002.csv',
 '/data/dumps/expC_dist_learner_for_adv_ex/rdm_concspheres_test/rdm_concspheres_k50n500_noninfdist/1/attack_perf/atk_flavor=std_pgd,atk_routine=my,eps=0.01,eps_iter=0.005,nb_iter=100,norm=2,restarts=1,verbose=False,task=dist/abs_cm_plots_test/abs_cm_test_th=0.15000000000000002.csv',
 '/data/dumps/expC_dist_learner_for_adv_ex/rdm_concspheres_test/rdm_concspheres_k50n500_noninfdist/1/attack_perf/atk_flavor=std_pgd,atk_routine=my,e

In [40]:
x = unique_runs_to_check_for_thresh.drop(["adv_clf_report", "clf_report"], axis=1)
x.drop_duplicates()

atk_flavor atk_routine   eps  eps_iter  nb_iter  norm  restarts  verbose  \
0      std_pgd          my  0.01     0.005      100     2         1    False   
16     std_pgd          my  0.01     0.006      100     2         1    False   
32     std_pgd          my  0.01     0.007      100     2         1    False   
48     std_pgd          my  0.01     0.008      100     2         1    False   
64     std_pgd          my  0.01     0.009      100     2         1    False   
80     std_pgd          my  0.02     0.005      100     2         1    False   
96     std_pgd          my  0.02     0.006      100     2         1    False   
112    std_pgd          my  0.02     0.007      100     2         1    False   
128    std_pgd          my  0.02     0.008      100     2         1    False   
144    std_pgd          my  0.02     0.009      100     2         1    False   
160    std_pgd          my  0.03     0.005      100     2         1    False   
176    std_pgd          my  0.03     0.006      100     2         1    False   
192    std_pgd          my  0.03     0.007      100     2         1    False   
208    std_pgd          my  0.03     0.008      100     2         1    False   
224    std_pgd          my  0.03     0.009      100     2         1    False   
240    std_pgd          my  0.04     0.005      100     2         1    False   
256    std_pgd          my  0.04     0.006      100     2         1    False   
272    std_pgd          my  0.04     0.007      100     2         1    False   
288    std_pgd          my  0.04     0.008      100     2         1    False   
304    std_pgd          my  0.04     0.009      100     2         1    False   
320    std_pgd          my  0.05     0.005      100     2         1    False   
336    std_pgd          my  0.05     0.006      100     2         1    False   
352    std_pgd          my  0.05     0.007      100     2         1    False   
368    std_pgd          my  0.05     0.008      100     2         1    False   
384    std_pgd          my  0.05     0.009      100     2         1    False   
400    std_pgd          my  0.06     0.005      100     2         1    False   
416    std_pgd          my  0.06     0.006      100     2         1    False   
432    std_pgd          my  0.06     0.007      100     2         1    False   
448    std_pgd          my  0.06     0.008      100     2         1    False   
464    std_pgd          my  0.06     0.009      100     2         1    False   
480    std_pgd          my  0.07     0.005      100     2         1    False   
496    std_pgd          my  0.07     0.006      100     2         1    False   
512    std_pgd          my  0.07     0.007      100     2         1    False   
528    std_pgd          my  0.07     0.008      100     2         1    False   
544    std_pgd          my  0.07     0.009      100     2         1    False   
560    std_pgd          my  0.08     0.005      100     2         1    False   
576    std_pgd          my  0.08     0.006      100     2         1    False   
592    std_pgd          my  0.08     0.007      100     2         1    False   
608    std_pgd          my  0.08     0.008      100     2         1    False   
624    std_pgd          my  0.08     0.009      100     2         1    False   
640    std_pgd          my  0.09     0.005      100     2         1    False   
656    std_pgd          my  0.09     0.006      100     2         1    False   
672    std_pgd          my  0.09     0.007      100     2         1    False   
688    std_pgd          my  0.09     0.008      100     2         1    False   
704    std_pgd          my  0.09     0.009      100     2         1    False   
720    std_pgd          my  0.10     0.005      100     2         1    False   
736    std_pgd          my  0.10     0.006      100     2         1    False   
752    std_pgd          my  0.10     0.007      100     2         1    False   
768    std_pgd          my  0.10     0.008      100     2         1    False   
784 